In [ ]:
import os
import cv2
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from albumentations import (
    Compose, RandomBrightnessContrast, HueSaturationValue, GaussNoise, Blur,
    HorizontalFlip, VerticalFlip, Rotate
)

# Set the paths to the image and annotation folders
dataset_folder = "dataset"
train_folder = os.path.join(dataset_folder, "train")
sequences_folder = os.path.join(train_folder, "sequences")
annotations_folder = os.path.join(train_folder, "annotations")

In [32]:
# Function to read annotation file
def read_annotation_file(file_path):
    annotations = {}
    with open(file_path, "r") as file:
        for line in file:
            line = line.strip()
            if line:
                anno = line.split(",")
                frame_id = int(anno[0])
                if frame_id not in annotations:
                    annotations[frame_id] = []
                annotations[frame_id].append(anno)
    return annotations

def visualize_annotations(image, annotations):
    h, w = image.shape[:2]
    for anno in annotations:
        parts = anno.strip().split()
        if len(parts) >= 5:
            obj_id = int(parts[0])
            x_center, y_center, width, height = map(float, parts[1:5])
            
            # Convert YOLO format to pixel coordinates
            x = int((x_center - width/2) * w)
            y = int((y_center - height/2) * h)
            box_width = int(width * w)
            box_height = int(height * h)
            
            cv2.rectangle(image, (x, y), (x+box_width, y+box_height), (0, 255, 0), 2)
            cv2.putText(image, f"ID: {obj_id}", (x, y-5), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)
    
    plt.figure(figsize=(10, 8))
    plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    plt.axis("off")
    plt.show()

# Function to resize image and annotations
def resize_image_and_annotations(image, annotations, target_size=(416, 416)):
    h, w = image.shape[:2]
    resized_image = cv2.resize(image, target_size)
    scale_x, scale_y = target_size[0] / w, target_size[1] / h
    
    resized_annotations = []
    for anno in annotations:
        obj_id, x, y, w, h = int(anno[1]), float(anno[2]), float(anno[3]), float(anno[4]), float(anno[5])
        new_x, new_y = x * scale_x, y * scale_y
        new_w, new_h = w * scale_x, h * scale_y
        
        # Ensure the bounding box is within the image boundaries
        new_x = max(0, min(new_x, target_size[0] - 1))
        new_y = max(0, min(new_y, target_size[1] - 1))
        new_w = max(1, min(new_w, target_size[0] - new_x))
        new_h = max(1, min(new_h, target_size[1] - new_y))
        
        resized_annotations.append([anno[0], obj_id, new_x, new_y, new_w, new_h] + anno[6:])
    
    return resized_image, resized_annotations

def apply_augmentation(image, annotations):
    aug = Compose([
        RandomBrightnessContrast(p=0.5),
        HueSaturationValue(p=0.5),
        GaussNoise(p=0.3),
        Blur(blur_limit=7, p=0.3),
        HorizontalFlip(p=0.5),
        VerticalFlip(p=0.3),
        Rotate(limit=30, p=0.5)
    ], bbox_params={'format': 'pascal_voc', 'label_fields': ['labels']})
    
    bboxes = [[anno[2], anno[3], anno[2]+anno[4], anno[3]+anno[5]] for anno in annotations]
    labels = [anno[1] for anno in annotations]
    
    try:
        augmented = aug(image=image, bboxes=bboxes, labels=labels)
        augmented_image = augmented['image']
        augmented_bboxes = augmented['bboxes']
        
        augmented_annotations = []
        for i, bbox in enumerate(augmented_bboxes):
            x, y, x2, y2 = bbox
            w, h = x2 - x, y2 - y
            augmented_annotations.append([annotations[i][0], labels[i], int(x), int(y), int(w), int(h)] + annotations[i][6:])
        
        return augmented_image, augmented_annotations
    except ValueError as e:
        print(f"Skipping augmentation due to error: {e}")
        return image, annotations

# Function to convert annotations to YOLO format
def convert_to_yolo_format(annotations, image_width, image_height):
    yolo_annotations = []
    for anno in annotations:
        obj_id, x, y, w, h = int(anno[1]), int(anno[2]), int(anno[3]), int(anno[4]), int(anno[5])
        x_center = (x + w / 2) / image_width
        y_center = (y + h / 2) / image_height
        width = w / image_width
        height = h / image_height
        yolo_annotations.append(f"{obj_id} {x_center} {y_center} {width} {height}")
    return yolo_annotations

In [ ]:
def preprocess_dataset():
    all_images = []
    all_annotations = []
    for sequence_folder in os.listdir(sequences_folder):
        sequence_path = os.path.join(sequences_folder, sequence_folder)
        image_folder = sequence_path
        annotation_file = os.path.join(annotations_folder, f"{sequence_folder}.txt")
        
        annotations_dict = read_annotation_file(annotation_file)
        
        for image_file in os.listdir(image_folder):
            if image_file.endswith(".jpg"):
                frame_id = int(image_file.split(".")[0])
                image_path = os.path.join(image_folder, image_file)
                image = cv2.imread(image_path)
                
                if frame_id in annotations_dict:
                    annotations = annotations_dict[frame_id]
                    
                    try:
                        # Resize image and annotations
                        resized_image, resized_annotations = resize_image_and_annotations(image, annotations)
                        
                        # Apply data augmentation
                        augmented_image, augmented_annotations = apply_augmentation(resized_image, resized_annotations)
                        
                        # Convert annotations to YOLO format
                        yolo_annotations = convert_to_yolo_format(augmented_annotations, augmented_image.shape[1], augmented_image.shape[0])
                        
                        all_images.append(augmented_image)
                        all_annotations.append(yolo_annotations)
                    except Exception as e:
                        print(f"Error processing image {image_file}: {e}")
                        continue
    
    return all_images, all_annotations

# Run the preprocessing pipeline
train_images, train_annotations = preprocess_dataset()
print(f"Number of training samples: {len(train_images)}")

# Visualize a sample preprocessed image
if train_images:
    sample_image = train_images[0]
    sample_annotations = train_annotations[0]
    visualize_annotations(sample_image, sample_annotations)
else:
    print("No valid images were processed.")

In [64]:
import os
import yaml
from ultralytics import YOLO

In [63]:
# Save preprocessed data
preprocessed_folder = "preprocessed_data"
os.makedirs(preprocessed_folder, exist_ok=True)
train_folder = os.path.join(preprocessed_folder, "train")
os.makedirs(train_folder, exist_ok=True)

for i, (image, annotations) in enumerate(zip(train_images, train_annotations)):
    cv2.imwrite(os.path.join(train_folder, f"image_{i}.jpg"), image)
    with open(os.path.join(train_folder, f"image_{i}.txt"), "w") as f:
        for anno in annotations:
            f.write(f"{anno}\n")

In [67]:
# Define the content for visdrone_data.yaml
visdrone_data_content = {
    "path": os.path.abspath(preprocessed_folder),
    "train": "train",
    "val": "train",  # Using the same data for validation as we don't have a separate val set
    "nc": 10,
    "names": ['pedestrian', 'people', 'bicycle', 'car', 'van', 'truck', 'tricycle', 'awning-tricycle', 'bus', 'motor']
}

In [ ]:
# Create visdrone_data.yaml
yaml_path = "visdrone_data.yaml"
with open(yaml_path, "w") as f:
    yaml.dump(visdrone_data_content, f, default_flow_style=False)

print(f"Created {yaml_path}")

In [ ]:
# Verify paths
for key in ['train', 'val']:
    full_path = os.path.join(visdrone_data_content['path'], visdrone_data_content[key])
    if not os.path.exists(full_path):
        raise FileNotFoundError(f"{key} path does not exist: {full_path}")
    print(f"Verified {key} path: {full_path}")

In [ ]:
# Count images in train folder
train_images = len([f for f in os.listdir(train_folder) if f.endswith('.jpg')])
print(f"Number of training images: {train_images}")

# Load a pre-trained YOLOv8s model
model = YOLO('yolov8s.pt')

# Train the model using the preprocessed VisDrone dataset
results = model.train(
    data=yaml_path,
    epochs=100,
    imgsz=640,
    batch=16,
    name='yolov8s_visdrone_preprocessed'
)

In [3]:
def read_annotation_file(file_path):
    annotations = {}
    with open(file_path, "r") as file:
        for line in file:
            line = line.strip()
            if line:
                anno = line.split(",")
                frame_id = int(anno[0])
                if frame_id not in annotations:
                    annotations[frame_id] = []
                annotations[frame_id].append(anno)
    return annotations

def resize_image_and_annotations(image, annotations, target_size=(640, 640)):
    h, w = image.shape[:2]
    resized_image = cv2.resize(image, target_size)
    scale_x, scale_y = target_size[0] / w, target_size[1] / h
    
    resized_annotations = []
    for anno in annotations:
        obj_id, x, y, w, h = int(anno[1]), float(anno[2]), float(anno[3]), float(anno[4]), float(anno[5])
        new_x, new_y = x * scale_x, y * scale_y
        new_w, new_h = w * scale_x, h * scale_y
        
        # Ensure the bounding box is within the image boundaries
        new_x = max(0, min(new_x, target_size[0] - 1))
        new_y = max(0, min(new_y, target_size[1] - 1))
        new_w = max(1, min(new_w, target_size[0] - new_x))
        new_h = max(1, min(new_h, target_size[1] - new_y))
        
        resized_annotations.append([anno[0], obj_id, new_x, new_y, new_w, new_h] + anno[6:])
    
    return resized_image, resized_annotations

def convert_to_yolo_format(annotations, image_width, image_height):
    yolo_annotations = []
    for anno in annotations:
        obj_id, x, y, w, h = int(anno[1]), float(anno[2]), float(anno[3]), float(anno[4]), float(anno[5])
        x_center = (x + w / 2) / image_width
        y_center = (y + h / 2) / image_height
        width = w / image_width
        height = h / image_height
        yolo_annotations.append(f"{obj_id} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}")
    return yolo_annotations

def preprocess_validation_dataset(sequences_folder, annotations_folder, output_folder):
    os.makedirs(output_folder, exist_ok=True)
    processed_count = 0
    error_count = 0

    for sequence_folder in os.listdir(sequences_folder):
        if sequence_folder.endswith('.cache'):
            continue  # Skip cache files
        
        sequence_path = os.path.join(sequences_folder, sequence_folder)
        image_folder = sequence_path
        annotation_file = os.path.join(annotations_folder, f"{sequence_folder}.txt")
        
        if not os.path.exists(annotation_file):
            print(f"Warning: Annotation file not found for {sequence_folder}")
            continue

        annotations_dict = read_annotation_file(annotation_file)
        
        for image_file in os.listdir(image_folder):
            if image_file.endswith(".jpg"):
                frame_id = int(image_file.split(".")[0])
                image_path = os.path.join(image_folder, image_file)
                
                try:
                    image = cv2.imread(image_path)
                    if image is None:
                        raise ValueError(f"Failed to read image: {image_path}")

                    if frame_id in annotations_dict:
                        annotations = annotations_dict[frame_id]
                        
                        # Resize image and annotations
                        resized_image, resized_annotations = resize_image_and_annotations(image, annotations)
                        
                        # Convert annotations to YOLO format
                        yolo_annotations = convert_to_yolo_format(resized_annotations, resized_image.shape[1], resized_image.shape[0])
                        
                        # Save resized image
                        output_image_path = os.path.join(output_folder, f"{sequence_folder}_{image_file}")
                        cv2.imwrite(output_image_path, resized_image)
                        
                        # Save YOLO annotations
                        output_anno_path = os.path.join(output_folder, f"{sequence_folder}_{image_file.rsplit('.', 1)[0]}.txt")
                        with open(output_anno_path, 'w') as f:
                            for anno in yolo_annotations:
                                f.write(f"{anno}\n")
                        
                        processed_count += 1
                    else:
                        print(f"Warning: No annotations found for frame {frame_id} in {sequence_folder}")
                
                except Exception as e:
                    print(f"Error processing image {image_file} in {sequence_folder}: {e}")
                    error_count += 1
                    continue

    print(f"Preprocessing complete. Processed {processed_count} images. Encountered {error_count} errors.")
    return output_folder

# Usage example
if __name__ == "__main__":
    dataset_folder = "dataset"
    val_sequences_folder = os.path.join(dataset_folder, "val", "sequences")
    val_annotations_folder = os.path.join(dataset_folder, "val", "annotations")
    output_folder = "preprocessed_validation"

    preprocessed_val_folder = preprocess_validation_dataset(val_sequences_folder, val_annotations_folder, output_folder)
    print(f"Preprocessed validation data saved to: {preprocessed_val_folder}")

    # You can now update your YAML file to use this preprocessed_val_folder for validation

Preprocessing complete. Processed 2846 images. Encountered 0 errors.
Preprocessed validation data saved to: preprocessed_validation


In [4]:
import os

preprocessed_val_folder = "preprocessed_validation"
sample_label_file = os.path.join(preprocessed_val_folder, "uav0000086_00000_v_0000001.txt")

print("Sample label file content:")
with open(sample_label_file, 'r') as f:
    content = f.read()
    print(content)

# Check if the content looks like YOLO format
lines = content.strip().split('\n')
for line in lines:
    parts = line.split()
    if len(parts) == 5 and all(part.replace('.', '', 1).isdigit() for part in parts):
        print("This line appears to be in YOLO format.")
    else:
        print(f"This line may not be in YOLO format: {line}")

Sample label file content:
1 0.199405 0.410714 0.016369 0.059524
2 0.220610 0.417989 0.011161 0.047619
3 0.236979 0.407407 0.014137 0.047619
4 0.331101 0.279101 0.017857 0.052910
5 0.502976 0.314815 0.034226 0.058201
8 0.245908 0.405423 0.015625 0.062169
9 0.229167 0.394841 0.017857 0.054233
11 0.503348 0.457672 0.023065 0.100529
12 0.489583 0.558201 0.028274 0.116402
13 0.514881 0.509921 0.023810 0.109788
14 0.569568 0.618386 0.039435 0.123016
15 0.466890 0.521825 0.026042 0.117725
16 0.482515 0.447751 0.020089 0.093915
17 0.627976 0.484127 0.023810 0.108466
18 0.664435 0.443783 0.017857 0.107143
22 0.389881 0.717593 0.029762 0.165344
23 0.396949 0.402116 0.017113 0.068783
24 0.414807 0.388889 0.023065 0.066138
25 0.414062 0.398810 0.020089 0.067460
26 0.283482 0.708995 0.040179 0.148148
27 0.566220 0.396164 0.022321 0.054233
28 0.189360 0.438492 0.020089 0.101852
29 0.242188 0.271825 0.017113 0.070106
30 0.217262 0.313492 0.014881 0.074074
32 0.306548 0.279762 0.040179 0.051587
33 0.

In [5]:
import os
import yaml
from ultralytics import YOLO

# Set the path to your trained model
model_path = 'runs/detect/yolov8s_visdrone_preprocessed/weights/best.pt'  # Adjust this path as needed

# Load the trained model
model = YOLO(model_path)

# Set the path to your preprocessed validation data
preprocessed_val_folder = "preprocessed_validation"  # Adjust this path if needed

# Update the data YAML file
yaml_path = "visdrone_data_preprocessed.yaml"
yaml_content = {
    "path": os.path.abspath(preprocessed_val_folder),  # Changed this line
    "train": "./",  # This is a placeholder, not used for validation
    "val": "./",
    "nc": 10,
    "names": ['pedestrian', 'people', 'bicycle', 'car', 'van', 'truck', 'tricycle', 'awning-tricycle', 'bus', 'motor']
}

# Write the updated YAML file
with open(yaml_path, "w") as f:
    yaml.dump(yaml_content, f, default_flow_style=False)

# Print YAML content for verification
print("\nYAML Content:")
print(yaml.dump(yaml_content, default_flow_style=False))

# Run validation
try:
    results = model.val(data=yaml_path, imgsz=640, batch=16)
    print(f"\nValidation Results:")
    print(results)
except Exception as e:
    print(f"An error occurred during validation: {e}")
    print("Please check your dataset structure and YAML file configuration.")


YAML Content:
names:
- pedestrian
- people
- bicycle
- car
- van
- truck
- tricycle
- awning-tricycle
- bus
- motor
nc: 10
path: c:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation
train: ./
val: ./

Ultralytics YOLOv8.2.70  Python-3.11.7 torch-2.3.1+cpu CPU (11th Gen Intel Core(TM) i7-1165G7 2.80GHz)
Model summary (fused): 168 layers, 11,129,454 parameters, 0 gradients, 28.5 GFLOPs


val: Scanning C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation.cache... 2846 images, 0 backgrounds, 2846 corrupt: 100%|██████████| 2846/2846 [00:00<?, ?it/s]

val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000001.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000002.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000003.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000004.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000005.jpg: ignorin

In [ ]:
from ultralytics import YOLO
from ultralytics.data.dataset import YOLODataset

# Load the YAML file
yaml_path = "visdrone_data_preprocessed.yaml"

# Try to create a YOLODataset
try:
    dataset = YOLODataset(yaml_path, task='detect')
    print(f"Dataset loaded successfully. Number of images: {len(dataset)}")
    
    # Check the first few items
    for i in range(min(5, len(dataset))):
        item = dataset[i]
        print(f"\nItem {i}:")
        print(f"Image shape: {item[0].shape}")
        print(f"Labels shape: {item[1].shape}")
except Exception as e:
    print(f"An error occurred while loading the dataset: {e}")

In [6]:
import os

preprocessed_val_folder = "preprocessed_validation"
sample_label_file = os.path.join(preprocessed_val_folder, "uav0000086_00000_v_0000001.txt")

print("Sample label file content:")
with open(sample_label_file, 'r') as f:
    content = f.read()
    print(content)

# Collect all unique class IDs
class_ids = set()
for label_file in os.listdir(preprocessed_val_folder):
    if label_file.endswith('.txt'):
        with open(os.path.join(preprocessed_val_folder, label_file), 'r') as f:
            for line in f:
                class_id = int(line.split()[0])
                class_ids.add(class_id)

print("\nUnique class IDs found in labels:")
print(sorted(class_ids))

Sample label file content:
1 0.199405 0.410714 0.016369 0.059524
2 0.220610 0.417989 0.011161 0.047619
3 0.236979 0.407407 0.014137 0.047619
4 0.331101 0.279101 0.017857 0.052910
5 0.502976 0.314815 0.034226 0.058201
8 0.245908 0.405423 0.015625 0.062169
9 0.229167 0.394841 0.017857 0.054233
11 0.503348 0.457672 0.023065 0.100529
12 0.489583 0.558201 0.028274 0.116402
13 0.514881 0.509921 0.023810 0.109788
14 0.569568 0.618386 0.039435 0.123016
15 0.466890 0.521825 0.026042 0.117725
16 0.482515 0.447751 0.020089 0.093915
17 0.627976 0.484127 0.023810 0.108466
18 0.664435 0.443783 0.017857 0.107143
22 0.389881 0.717593 0.029762 0.165344
23 0.396949 0.402116 0.017113 0.068783
24 0.414807 0.388889 0.023065 0.066138
25 0.414062 0.398810 0.020089 0.067460
26 0.283482 0.708995 0.040179 0.148148
27 0.566220 0.396164 0.022321 0.054233
28 0.189360 0.438492 0.020089 0.101852
29 0.242188 0.271825 0.017113 0.070106
30 0.217262 0.313492 0.014881 0.074074
32 0.306548 0.279762 0.040179 0.051587
33 0.

In [ ]:
import os

def correct_labels(input_folder, output_folder):
    os.makedirs(output_folder, exist_ok=True)
    
    # First, find all unique class IDs
    class_ids = set()
    for label_file in os.listdir(input_folder):
        if label_file.endswith('.txt'):
            with open(os.path.join(input_folder, label_file), 'r') as f:
                for line in f:
                    class_id = int(line.split()[0])
                    class_ids.add(class_id)
    
    # Create a mapping from old class IDs to new class IDs (0 to 9)
    class_mapping = {old_id: new_id for new_id, old_id in enumerate(sorted(class_ids))}
    
    print("Class ID mapping:")
    print(class_mapping)
    
    # Now, correct the label files
    for label_file in os.listdir(input_folder):
        if label_file.endswith('.txt'):
            with open(os.path.join(input_folder, label_file), 'r') as f:
                lines = f.readlines()
            
            corrected_lines = []
            for line in lines:
                parts = line.split()
                old_class_id = int(parts[0])
                new_class_id = class_mapping[old_class_id]
                corrected_line = f"{new_class_id} {' '.join(parts[1:])}\n"
                corrected_lines.append(corrected_line)
            
            with open(os.path.join(output_folder, label_file), 'w') as f:
                f.writelines(corrected_lines)
        
        # Copy corresponding image file
        image_file = label_file.rsplit('.', 1)[0] + '.jpg'
        if os.path.exists(os.path.join(input_folder, image_file)):
            os.system(f'copy "{os.path.join(input_folder, image_file)}" "{os.path.join(output_folder, image_file)}"')

    print(f"Corrected labels and copied images to {output_folder}")

# Usage
input_folder = "preprocessed_validation"
output_folder = "corrected_validation"
correct_labels(input_folder, output_folder)

In [7]:
import os
import yaml
from ultralytics import YOLO
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

# Set the path to your trained model
model_path = 'runs/detect/yolov8s_visdrone_preprocessed/weights/best.pt'  # Adjust this path as needed

# Load the trained model
model = YOLO(model_path)

# Set the path to your corrected validation data
corrected_val_folder = "corrected_validation"  # This should match the path in your YAML file

# YAML file path
yaml_path = "visdrone_data.yaml"

# Run validation
try:
    results = model.val(data=yaml_path, imgsz=640, batch=16)
    print(f"\nValidation Results:")
    print(results)

    # Extract metrics
    metrics = results.results_dict

    # 1. Overall Metrics Bar Plot
    overall_metrics = ['precision', 'recall', 'mAP50', 'mAP50-95']
    values = [metrics[m] for m in overall_metrics]

    plt.figure(figsize=(10, 6))
    sns.barplot(x=overall_metrics, y=values)
    plt.title('Overall Model Performance')
    plt.ylabel('Score')
    plt.ylim(0, 1)
    for i, v in enumerate(values):
        plt.text(i, v, f'{v:.3f}', ha='center', va='bottom')
    plt.tight_layout()
    plt.savefig('overall_metrics.png')
    plt.close()

    # 2. Per-class Metrics Heatmap
    class_names = results.names
    metrics_names = ['precision', 'recall', 'mAP50', 'mAP50-95']
    class_metrics = np.array([[metrics[f'{m}_per_class'][i] for m in metrics_names] for i in range(len(class_names))])

    plt.figure(figsize=(12, 10))
    sns.heatmap(class_metrics, annot=True, fmt='.3f', xticklabels=metrics_names, yticklabels=class_names, cmap='YlGnBu')
    plt.title('Per-class Performance Metrics')
    plt.tight_layout()
    plt.savefig('per_class_metrics_heatmap.png')
    plt.close()

    # 3. Confusion Matrix
    conf_matrix = results.confusion_matrix.matrix
    conf_matrix_norm = conf_matrix / conf_matrix.sum(axis=1, keepdims=True)

    plt.figure(figsize=(12, 10))
    sns.heatmap(conf_matrix_norm, annot=True, fmt='.2f', xticklabels=class_names, yticklabels=class_names, cmap='Blues')
    plt.title('Normalized Confusion Matrix')
    plt.xlabel('Predicted')
    plt.ylabel('True')
    plt.tight_layout()
    plt.savefig('confusion_matrix.png')
    plt.close()

    # 4. Sample Predictions
    sample_images = [os.path.join(corrected_val_folder, f) for f in os.listdir(corrected_val_folder) if f.endswith('.jpg')][:5]

    for i, img_path in enumerate(sample_images):
        results = model(img_path)
        fig, ax = plt.subplots(1, 1, figsize=(12, 8))
        res_plotted = results[0].plot()
        ax.imshow(res_plotted)
        ax.axis('off')
        ax.set_title(f"Sample Prediction {i+1}")
        plt.tight_layout()
        plt.savefig(f'sample_prediction_{i+1}.png')
        plt.close()

    print("\nVisualization complete. Check the current directory for the following plots:")
    print("1. overall_metrics.png")
    print("2. per_class_metrics_heatmap.png")
    print("3. confusion_matrix.png")
    print("4. sample_prediction_[1-5].png")

except Exception as e:
    print(f"An error occurred during validation or visualization: {e}")
    print("Please check your dataset structure and YAML file configuration.")

Ultralytics YOLOv8.2.70  Python-3.11.7 torch-2.3.1+cpu CPU (11th Gen Intel Core(TM) i7-1165G7 2.80GHz)
Model summary (fused): 168 layers, 11,129,454 parameters, 0 gradients, 28.5 GFLOPs


val: Scanning C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_data\train.cache... 24198 images, 0 backgrounds, 24082 corrupt: 100%|██████████| 24198/24198 [00:00<?, ?it/s]

train: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_data\train\image_0.jpg: ignoring corrupt image/label: Label class 59 exceeds dataset class count 10. Possible class labels are 0-9
train: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_data\train\image_1.jpg: ignoring corrupt image/label: Label class 59 exceeds dataset class count 10. Possible class labels are 0-9
train: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_data\train\image_10.jpg: ignoring corrupt image/label: Label class 59 exceeds dataset class count 10. Possible class labels are 0-9
train: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_data\train\image_100.jpg: ignoring corrupt image/label: Label class 59 exceeds dataset class count 10. Possible class labels are 0-9
train: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_data\train\image_1000.jpg: ignoring corrupt image/label: Label class 80 exceeds dataset class count 10. Possible 


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 8/8 [00:52<00:00,  6.55s/it]


                   all        116        837      0.945       0.98      0.986      0.801
            pedestrian        116        116      0.987          1      0.995      0.794
                people         39         39      0.986          1      0.995      0.893
               bicycle        102        102       0.98          1      0.995      0.876
                   car        116        116      0.912      0.991      0.989      0.751
                   van        116        116      0.852      0.966      0.971      0.716
                 truck        116        116      0.874      0.871      0.944      0.578
              tricycle        116        116      0.994          1      0.995      0.964
       awning-tricycle         15         15      0.936          1      0.991      0.751
                   bus        101        101      0.987       0.99      0.995       0.89
Speed: 3.3ms preprocess, 424.9ms inference, 0.0ms loss, 1.4ms postprocess per image
Results saved to runs\dete

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

# Assuming 'results' contains your validation results

# 1. Overall Metrics Bar Plot
metrics = results.results_dict
overall_metrics = ['metrics/precision(B)', 'metrics/recall(B)', 'metrics/mAP50(B)', 'metrics/mAP50-95(B)']
values = [metrics[m] for m in overall_metrics]

plt.figure(figsize=(10, 6))
sns.barplot(x=[m.split('/')[-1].split('(')[0] for m in overall_metrics], y=values)
plt.title('Overall Model Performance')
plt.ylabel('Score')
plt.ylim(0, 1)
for i, v in enumerate(values):
    plt.text(i, v, f'{v:.3f}', ha='center', va='bottom')
plt.tight_layout()
plt.savefig('overall_metrics.png')
plt.close()

# 2. Per-class Metrics Heatmap
class_names = results.names
metrics_names = ['precision', 'recall', 'mAP50', 'mAP50-95']
class_metrics = np.array([results.maps])  # Use the maps array directly

plt.figure(figsize=(12, 10))
sns.heatmap(class_metrics, annot=True, fmt='.3f', xticklabels=class_names.values(), yticklabels=['mAP'], cmap='YlGnBu')
plt.title('Per-class mAP')
plt.tight_layout()
plt.savefig('per_class_metrics_heatmap.png')
plt.close()

print("\nVisualization complete. Check the current directory for the following plots:")
print("1. overall_metrics.png")
print("2. per_class_metrics_heatmap.png")

In [8]:
import os
import yaml
from ultralytics import YOLO
import matplotlib.pyplot as plt
import seaborn as sns

# Set the path to your trained model
model_path = 'runs/detect/yolov8s_visdrone_preprocessed/weights/best.pt'  # Adjust this path as needed

# Load the trained model
model = YOLO(model_path)

# Set the path to your preprocessed validation data
preprocessed_val_folder = "preprocessed_validation"  # Adjust this path if needed

# Verify the preprocessed data
image_count = len([f for f in os.listdir(preprocessed_val_folder) if f.endswith('.jpg')])
label_count = len([f for f in os.listdir(preprocessed_val_folder) if f.endswith('.txt')])

print(f"Number of images in {preprocessed_val_folder}: {image_count}")
print(f"Number of label files in {preprocessed_val_folder}: {label_count}")

if image_count == 0 or label_count == 0:
    raise ValueError("No images or labels found in the preprocessed validation folder.")

# Update the data YAML file to include the preprocessed validation path
yaml_path = "visdrone_data_preprocessed.yaml"
yaml_content = {
    "path": os.path.abspath(os.path.dirname(preprocessed_val_folder)),
    "train": "train",  # Assuming you have a preprocessed training folder
    "val": os.path.basename(preprocessed_val_folder),
    "nc": 10,
    "names": ['pedestrian', 'people', 'bicycle', 'car', 'van', 'truck', 'tricycle', 'awning-tricycle', 'bus', 'motor']
}

# Write the updated YAML file
with open(yaml_path, "w") as f:
    yaml.dump(yaml_content, f, default_flow_style=False)

# Print YAML content for verification
print("\nYAML Content:")
print(yaml.dump(yaml_content, default_flow_style=False))

# Run validation
try:
    results = model.val(data=yaml_path, imgsz=640, batch=16)

    # Print overall metrics
    print(f"\nOverall mAP50: {results.box.map50:.3f}")
    print(f"Overall mAP50-95: {results.box.map:.3f}")

    # Get per-class metrics
    class_map50 = results.box.class_map50
    class_names = yaml_content['names']

    # Create a bar plot of mAP50 for each class
    plt.figure(figsize=(12, 6))
    sns.barplot(x=class_names, y=class_map50)
    plt.title('mAP50 by Class')
    plt.xlabel('Class')
    plt.ylabel('mAP50')
    plt.xticks(rotation=45, ha='right')
    plt.tight_layout()
    plt.savefig('map50_by_class.png')
    plt.close()

    # Print per-class metrics
    print("\nPer-class mAP50:")
    for name, map50 in zip(class_names, class_map50):
        print(f"{name}: {map50:.3f}")

    # Run inference on a few sample images from the preprocessed validation set
    sample_images = [os.path.join(preprocessed_val_folder, f) for f in os.listdir(preprocessed_val_folder) if f.endswith('.jpg')][:5]

    for img_path in sample_images:
        results = model(img_path)
        res_plotted = results[0].plot()
        plt.figure(figsize=(10, 10))
        plt.imshow(res_plotted)
        plt.axis('off')
        plt.title(f"Predictions on {os.path.basename(img_path)}")
        plt.savefig(f"prediction_{os.path.basename(img_path)}")
        plt.close()

    print("\nValidation complete. Check the output for metrics and the current directory for visualization plots.")
except Exception as e:
    print(f"An error occurred during validation: {e}")
    print("Please check your dataset structure and YAML file configuration.")

Number of images in preprocessed_validation: 2846
Number of label files in preprocessed_validation: 2846

YAML Content:
names:
- pedestrian
- people
- bicycle
- car
- van
- truck
- tricycle
- awning-tricycle
- bus
- motor
nc: 10
path: c:\Users\j.udahemuka\Desktop\drone dataset
train: train
val: preprocessed_validation

Ultralytics YOLOv8.2.70  Python-3.11.7 torch-2.3.1+cpu CPU (11th Gen Intel Core(TM) i7-1165G7 2.80GHz)
Model summary (fused): 168 layers, 11,129,454 parameters, 0 gradients, 28.5 GFLOPs


val: Scanning C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation.cache... 2846 images, 0 backgrounds, 2846 corrupt: 100%|██████████| 2846/2846 [00:00<?, ?it/s]

val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000001.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000002.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000003.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000004.jpg: ignoring corrupt image/label: Label class 55 exceeds dataset class count 10. Possible class labels are 0-9
val: WARNING  C:\Users\j.udahemuka\Desktop\drone dataset\preprocessed_validation\uav0000086_00000_v_0000005.jpg: ignorin